In [1]:
import sys
sys.path.append('../')

%load_ext autoreload
%autoreload 2

In [2]:
import numpy as np
import pandas as pd
import yfinance as yf

from sklearn.dummy import DummyRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error

import wavy
from wavy.models import compute_default_scores
from wavy.utils import reverse_pct_change
# from wavy.plot import 

In [3]:
tickers = pd.read_html('https://en.wikipedia.org/wiki/List_of_S%26P_500_companies')[0].Symbol

In [4]:
msft = yf.Ticker("MSFT")

In [5]:
# get historical market data from 2005 on
hist = msft.history(period="max", start="2005-01-01")

In [6]:
hist

Open        High         Low       Close     Volume  \
Date                                                                    
2005-01-03   19.040899   19.147472   18.934327   18.998270   65002900   
2005-01-04   19.090632   19.254042   18.941430   19.069317  109442100   
2005-01-05   19.069316   19.254041   19.012478   19.026688   72463500   
2005-01-06   19.076419   19.225620   18.927218   19.005371   76890500   
2005-01-07   19.055098   19.104832   18.913003   18.948526   68723300   
...                ...         ...         ...         ...        ...   
2022-04-18  278.910004  282.459991  278.339996  280.519989   20778000   
2022-04-19  279.380005  286.170013  278.410004  285.299988   22297700   
2022-04-20  289.399994  289.700012  285.369995  286.359985   22906700   
2022-04-21  288.579987  293.299988  280.059998  280.809998   29454600   
2022-04-22  281.679993  283.200012  273.380005  274.029999   29379300   

            Dividends  Stock Splits  
Date                                 
2005-01-03        0.0             0  
2005-01-04        0.0             0  
2005-01-05        0.0             0  
2005-01-06        0.0             0  
2005-01-07        0.0             0  
...               ...           ...  
2022-04-18        0.0             0  
2022-04-19        0.0             0  
2022-04-20        0.0             0  
2022-04-21        0.0             0  
2022-04-22        0.0             0  

[4357 rows x 7 columns]

In [7]:
hist[['Open', 'High', 'Low', 'Close']].plot()

In [8]:
hist = hist[['Open', 'High', 'Low', 'Close']]

In [9]:
df = hist.pct_change()

In [10]:
df.plot()

In [11]:
print(len(df) - len(df.dropna()))
df.dropna(inplace=True)

1


In [12]:
df.High.hist(bins=200)

In [13]:
x, y = wavy.create_panels(df, lookback=10, horizon=1)

In [14]:
x.columns

Index(['Open', 'High', 'Low', 'Close'], dtype='object')

In [15]:
x[0].Open

Date
2005-01-04    0.002612
2005-01-05   -0.001117
2005-01-06    0.000373
2005-01-07   -0.001118
2005-01-10   -0.008203
2005-01-11    0.003383
2005-01-12    0.002998
2005-01-13   -0.003362
2005-01-14   -0.010495
2005-01-18   -0.014015
Name: Open, dtype: float64

In [16]:
x.plot()

In [17]:
# predict only the highest price
y = y['High']

In [18]:
# try single col inputs first
x_high = x['High']

In [19]:
x_high.plot()

In [20]:
lr = wavy.models.LinearRegression(x_high, y)

In [22]:
lr.fit(epochs=10, verbose=False)
lr.score()

train       val      test
loss  0.000212  0.000200  0.000164
MAE   0.009561  0.009664  0.009383

In [23]:
baseline = wavy.models.BaselineConstant(x_high, y, model_type="regression", constant=0)
baseline.fit()
baseline.score()

98/98 [==============================] - 0s 1ms/step - loss: 0.0000e+00 - MAE: 0.0096 - val_loss: 0.0000e+00 - val_MAE: 0.0097


train       val      test
loss  0.000000  0.000000  0.000000
MAE   0.009568  0.009672  0.009435

In [24]:
y_pred = baseline.predict()

In [25]:
y.plot()

In [30]:
y_pred.plot()

In [26]:
rev_y = reverse_pct_change(y, hist)

../wavy/panel.py:570: UserWarning:

Sizes don't match. Using dataframe indexes and columns to update.



In [27]:
rev_y.plot()

In [28]:
rev_y_pred = reverse_pct_change(y_pred, hist)

../wavy/panel.py:570: UserWarning:

Sizes don't match. Using dataframe indexes and columns to update.



In [29]:
rev_y_pred.plot()

In [39]:
# How to interpret that error? What does it mean comparing to the mean/std of the val set?
np.median(baseline.y_val.flatten())

0.001530375015831975

In [42]:
residuals = baseline.residuals()

In [43]:
residuals.plot() # Highest error is in train set

In [47]:
compute_default_scores(x_high, y, 'regression', ['MAE', 'MSE'])

../wavy/models.py:155: UserWarning:

Filling nan values with 0



../wavy/models.py:286: UserWarning:

Kernel size is not a divisor of lookback.



loss       MAE       MSE
BaselineConstant  0.000000  0.009672  0.000200
BaselineShift     0.000407  0.013949  0.000407
DenseModel        0.000204  0.009720  0.000204
ConvModel         0.000205  0.009780  0.000205

In [ ]:
conv = wavy.ConvModel(x_high, y, model_type="regression", conv_layers=1, conv_filters=32,kernel_size=3, dense_layers=1, dense_units=32)
conv.fit(epochs=20)

# using a cannon ball to kill an ant!

In [ ]:
params=[{'conv_layers': [1, 5, 10], 'conv_filters': [16, 32], 'kernel_size': [2, 3, 7], 'dense_layers': [1], 'dense_units': [32]}, {'dense_layers': 1, 'dense_units': 32}]

models = [ConvModel, DenseModel]

# wavy.GridSearchModel(x, y, model_type, models=, )

In [ ]:
lr.score()

In [ ]:
grid_search --> sklearn

In [ ]:
conv.plot_residuals()

In [ ]:
# TODO: Compare residuals between models

In [ ]:
default_scores = compute_default_scores(x, y, model_type="regression", metrics=["MAE", "MSE"])

In [ ]:
# rev_y = reverse_pct_change(y, hist).as_dataframe()
# rev_y_conv = reverse_pct_change(conv.predict(), hist).as_dataframe()
# rev_y_base = reverse_pct_change(baseline.predict(), hist).as_dataframe()

# rev_y_conv.columns = ['conv_' + col for col in rev_y_conv.columns]
# rev_y_base.columns = ['base_' + col for col in rev_y_base.columns]

In [ ]:
# plot_dataframes([rev_y, rev_y_conv, rev_y_base])

In [ ]:
y_pred[0]

In [ ]:
hist.iloc[10:20]

In [ ]:
y_orig.as_dataframe()

In [ ]:
y.as_dataframe()

In [ ]:
y_orig = y.update(hist.shift())

In [ ]:
y_orig[0]

In [ ]:
y_pred_orig = y_pred.shift() + y_orig

In [ ]:
y_pred_orig.plot()

In [ ]:
y_true = y.test.as_dataframe()
y_baseline = baseline.predict().as_dataframe()
y_lr = lr.predict().as_dataframe()
y_dense = dense.predict().as_dataframe()
y_conv = conv.predict().as_dataframe()

y_true.columns = ['true_' + col for col in y_true.columns]
y_baseline.columns = ['baseline_' + col for col in y_baseline.columns]
y_lr.columns = ['lr_' + col for col in y_lr.columns]
y_dense.columns = ['dense_' + col for col in y_dense.columns]
y_conv.columns = ['conv_' + col for col in y_conv.columns]

plot_dataframes([y_true, y_baseline, y_lr, y_dense, y_conv])

In [ ]:
baseline

In [ ]:
dummy = wavy.ShallowModel(x_high, y, model=DummyRegressor, metrics=[mean_absolute_error], strategy="mean")
dummy.fit()

In [ ]:
rf = wavy.ShallowModel(x, y, model=RandomForestRegressor, metrics=[mean_absolute_error], n_estimators=50)
rf.fit()

In [ ]:
dense = wavy.DenseModel(x, y, model_type="regression")
dense.fit(epochs=20)

In [ ]:
# Try the same models but with all input columns
# TODO: Use function to compute default results per model

# lr = wavy.LinearRegression(x, y)
# lr.fit(epochs=20)

In [ ]:

# data1 = {'train': x.train.as_dataframe()["High"],
#         'val': x.val.as_dataframe()["High"],
#         'test': x.test.as_dataframe()["High"]
#         }

# data2 = {'train': x.train.as_dataframe()["Low"],
#         'val': x.val.as_dataframe()["Low"],
#         'test': x.test.as_dataframe()["Low"]
#         }

In [ ]:
aaa = y[-1000:]

s1 = y.train.as_dataframe()['High']
s2 = y.val.as_dataframe()['High']
s3 = y.test.as_dataframe()['High']

In [ ]:
fig = Figure()

In [ ]:
# fig.linebar(s)
# fig.scatter(s)

fig.dotbar(s1)
fig.dotbar(s2, color="blue")
fig.dotbar(s3)

In [ ]:
fig.fig

In [ ]:
fig = PanelFigure()
fig.split_sets(data1)
fig.add_area(data1)
fig.add_dotbar(data2)

In [ ]:
fig.compile()